In [2]:
import pandas as pd
#import geopandas as gpd
import re
import matplotlib.pyplot as plt
from matplotlib.widgets import Slider
import plotly.express as px



In [3]:

#change this function to store different data
def read_and_store_herring_data(year):
    string ='fangstdata\elektronisk-rapportering-ers-' + str(year) + '-fangstmelding-dca.csv'
    catch_data = pd.read_csv(string,delimiter=';', on_bad_lines='skip', encoding='utf8')
    herring_catches = catch_data.loc[catch_data['Art - FDIR'] == 'Sild']
    longitude = pd.to_numeric([pos.replace(',','.') for pos in herring_catches['Startposisjon bredde']])
    latitude = pd.to_numeric([pos.replace(',','.') for pos in herring_catches['Startposisjon lengde']])
    Rundvekt = pd.to_numeric([vekt for vekt in herring_catches['Rundvekt']])
    month = pd.to_numeric([date.split('.')[1] for date in herring_catches['Meldingsdato']]) #henter ut måned for fangst
    catch_year = pd.to_numeric([date.split('.')[2] for date in herring_catches['Meldingsdato']])
    data = {'longitude': longitude,
        'latitude': latitude,
        'Rundvekt': Rundvekt,
        'month': month,
        'year':  catch_year
    }
    df = pd.DataFrame(data)
    df.to_csv('cleaned_datasets/herring_catches_'+str(year)+'.csv')

for year in range(2011, 2021):
    if year in [2018, 2018, 2020]: pass
    read_and_store_herring_data(year)

C:\Users\evenasm\AppData\Local\Temp\ipykernel_8652\2536463212.py:4: DtypeWarning: Columns (77,78) have mixed types. Specify dtype option on import or set low_memory=False.
  catch_data = pd.read_csv(string,delimiter=';', on_bad_lines='skip', encoding='utf8')
C:\Users\evenasm\AppData\Local\Temp\ipykernel_8652\2536463212.py:4: DtypeWarning: Columns (51,77,78) have mixed types. Specify dtype option on import or set low_memory=False.
  catch_data = pd.read_csv(string,delimiter=';', on_bad_lines='skip', encoding='utf8')
C:\Users\evenasm\AppData\Local\Temp\ipykernel_8652\2536463212.py:4: DtypeWarning: Columns (51,83,90) have mixed types. Specify dtype option on import or set low_memory=False.
  catch_data = pd.read_csv(string,delimiter=';', on_bad_lines='skip', encoding='utf8')
C:\Users\evenasm\AppData\Local\Temp\ipykernel_8652\2536463212.py:4: DtypeWarning: Columns (51,83,90) have mixed types. Specify dtype option on import or set low_memory=False.
  catch_data = pd.read_csv(string,delimite

In [5]:
fangst_data_2018 = pd.read_csv('cleaned_datasets/herring_catches_2018.csv', on_bad_lines='skip', encoding='utf8')
fangst_data_2019 = pd.read_csv('cleaned_datasets/herring_catches_2019.csv', on_bad_lines='skip', encoding='utf8')
fangst_data_2020 = pd.read_csv('cleaned_datasets/herring_catches_2020.csv', on_bad_lines='skip', encoding='utf8')
fangst_data = []
for year in range(2011, 2020): 
    fangst_data.append(pd.read_csv('cleaned_datasets/herring_catches_'+str(year)+'.csv', on_bad_lines='skip', encoding='utf8'))
#print(fangst_data_2018.head)
#fangst_data_2018.merge(fangst_data_2019)
#fangst_data_2018.merge(fangst_data_2020)
#print(fangst_data_2018.head)
fangst_totalt = pd.concat(fangst_data)

fangst_desember = fangst_totalt.loc[fangst_totalt['month'] ==12]
fangst_januar = fangst_totalt.loc[fangst_totalt['month'] == 1]
fangst_desember_og_januar = pd.concat([fangst_desember, fangst_januar])



In [6]:
#for i in range(len(Rundvekt)):
#    if Rundvekt[i] == 0:
#        Rundvekt[i] = 1
#plotter = {'latitude' : latitude, 'longitude': longitude, 'Rundvekt':Rundvekt, 'month': month}

#fig = px.density_mapbox(plotter, lat='longitude', lon='latitude',mapbox_style='stamen-terrain', opacity=.7, radius=5, title="Sildefangst 2018")
def scatterplot_on_map(df, _title, _color):
    fig = px.scatter_mapbox(df, lat='longitude', lon='latitude',color=_color, size='Rundvekt',
        center=dict(lat=65, lon=10),mapbox_style='stamen-terrain', title=_title,
        height=1000, zoom=4)

    fig.show()


<h3>Noen interessante plots kommer her, først,  et plott over 3 år med desember/januarfangst. Legg merke til 3 samlinger: <h3>

-  Kvænangen (Troms og Finnmark)
-  Til havs vest for Bodø
-  Mellom orknaøyene og Bergen (minst insidens)

In [7]:
scatterplot_on_map(fangst_desember_og_januar, 'Sildefangst desember/januar 2011-2020', 'year')

<h3> Deretter har vi generell sildefangst per år, 2018, 2019 og 2020: </h3>

In [95]:
scatterplot_on_map(fangst_data_2018, 'Sildefangst 2018', 'month')

In [90]:
scatterplot_on_map(fangst_data_2019, 'Sildefangst 2019', 'month')

In [91]:
scatterplot_on_map(fangst_data_2020, 'Sildefangst 2020', 'month')

<h3> Total sildefangst over alle måneder i 3 år, farget etter år: </h3>

In [8]:
scatterplot_on_map(fangst_totalt, "Total fangst 2011-2020", 'year')

<h3> Total sildefangst 18/19/20, farget etter måned: </h3>

In [99]:
scatterplot_on_map(fangst_totalt, 'Sildefangst 18/19/20', 'month')